# Training & Generation

For training we use [OpenNMT-py](http://opennmt.net/OpenNMT-py/) which is based on PyTorch. This is a run-of-the mill Seq2Seq library that is traditionally used for neural machine translation.

I have forked their repository and adapted the code to incorporate ideas from [Stay On-Topic: Generating
Context-specific Fake Restaurant Reviews](https://arxiv.org/pdf/1805.02400.pdf)

Namely, during generation (beam-search) some words of the vocabulary will be randomly penalized, on top of that, recurring words will be penalized as well. I've also adapted the `-ignore_when_blocking` parameter from OpenNMT to reduce the penalty for certain 'anchor' words. Unlike the paper, this reduced penalty is only active after the first step and not for step 0.

Unlike the paper quoted above, I also did not add an obfuscation step.

My fork can be found under:

https://github.com/hokkaido/OpenNMT-py/tree/translate-improvements

The changes can be found at https://github.com/hokkaido/OpenNMT-py/pull/1/files

## Training

OpenNMT requires a preprocessing step, we limit the vocabulary size by specifying `-tgt_words_min_frequency`

In [3]:
!python /home/baoxiong/SY_269/OpenNMT-py/preprocess.py -train_src /home/baoxiong/SY_269/data/train_context.txt -train_tgt /home/baoxiong/SY_269/data/train_reviews.txt -valid_src /home/baoxiong/SY_269/data/test_context.txt -valid_tgt /home/baoxiong/SY_269/data/test_reviews.txt -save_data /home/baoxiong/SY_269/models/model15k -tgt_words_min_frequency 10

[2020-11-28 12:27:09,451 INFO] Extracting features...
[2020-11-28 12:27:09,453 INFO]  * number of source features: 0.
[2020-11-28 12:27:09,453 INFO]  * number of target features: 0.
[2020-11-28 12:27:09,453 INFO] Building `Fields` object...
[2020-11-28 12:27:09,453 INFO] Building & saving training data...
[2020-11-28 12:27:09,453 INFO] Reading source and target files: /home/baoxiong/SY_269/data/train_context.txt /home/baoxiong/SY_269/data/train_reviews.txt.
[2020-11-28 12:27:09,454 INFO] Building shard 0.
[2020-11-28 12:27:09,491 INFO]  * saving 0th train data shard to /home/baoxiong/SY_269/models/model15k.train.0.pt.
[2020-11-28 12:27:09,540 INFO]  * tgt vocab size: 529.
[2020-11-28 12:27:09,541 INFO]  * src vocab size: 1299.
[2020-11-28 12:27:09,549 INFO] Building & saving validation data...
[2020-11-28 12:27:09,549 INFO] Reading source and target files: /home/baoxiong/SY_269/data/test_context.txt /home/baoxiong/SY_269/data/test_reviews.txt.
[2020-11-28 12:27:09,551 INFO] Building sh

After that we can train the model as follows:

In [4]:
!CUDA_VISIBLE_DEVICES=0 python  /home/baoxiong/SY_269/OpenNMT-py/train.py --data /home/baoxiong/SY_269/models/model15k --save_model /home/baoxiong/SY_269/models/model15k750k --train_steps 750000 --learning_rate_decay 0.5 --optim adam --learning_rate 0.001 --start_decay_steps 281250 --world_size 1 --gpu_ranks 0 --batch_size 64

[2020-11-28 12:27:16,787 INFO]  * src vocab size = 1299
[2020-11-28 12:27:16,787 INFO]  * tgt vocab size = 529
[2020-11-28 12:27:16,787 INFO] Building model...
[2020-11-28 12:27:18,237 INFO] NMTModel(
  (encoder): RNNEncoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(1299, 500, padding_idx=1)
        )
      )
    )
    (rnn): LSTM(500, 500, num_layers=2, dropout=0.3)
  )
  (decoder): InputFeedRNNDecoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(529, 500, padding_idx=1)
        )
      )
    )
    (dropout): Dropout(p=0.3)
    (rnn): StackedLSTM(
      (dropout): Dropout(p=0.3)
      (layers): ModuleList(
        (0): LSTMCell(1000, 500)
        (1): LSTMCell(500, 500)
      )
    )
    (attn): GlobalAttention(
      (linear_in): Linear(in_features=500, out_features=500, bias=False)
      (linear_out): Linear(in_features=10

[2020-11-28 12:27:58,743 INFO] Step 1200/750000; acc:  65.89; ppl:  3.78; xent: 1.33; lr: 0.00100; 7376/25581 tok/s;     41 sec
[2020-11-28 12:27:58,743 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:27:58,752 INFO] number of examples: 3035
[2020-11-28 12:28:00,343 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:28:00,351 INFO] number of examples: 3035
[2020-11-28 12:28:00,435 INFO] Step 1250/750000; acc:  67.86; ppl:  3.50; xent: 1.25; lr: 0.00100; 7810/26945 tok/s;     42 sec
[2020-11-28 12:28:01,947 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:28:01,954 INFO] number of examples: 3035
[2020-11-28 12:28:02,129 INFO] Step 1300/750000; acc:  69.00; ppl:  3.30; xent: 1.19; lr: 0.00100; 7533/26956 tok/s;     44 sec
[2020-11-28 12:28:03,538 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:28:03,561 INFO] number of exa

[2020-11-28 12:28:45,821 INFO] number of examples: 3035
[2020-11-28 12:28:46,076 INFO] Step 2600/750000; acc:  90.68; ppl:  1.43; xent: 0.36; lr: 0.00100; 7587/26717 tok/s;     88 sec
[2020-11-28 12:28:47,438 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:28:47,447 INFO] number of examples: 3035
[2020-11-28 12:28:47,770 INFO] Step 2650/750000; acc:  90.68; ppl:  1.42; xent: 0.35; lr: 0.00100; 7735/26641 tok/s;     90 sec
[2020-11-28 12:28:49,047 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:28:49,054 INFO] number of examples: 3035
[2020-11-28 12:28:49,439 INFO] Step 2700/750000; acc:  91.20; ppl:  1.39; xent: 0.33; lr: 0.00100; 7777/27291 tok/s;     91 sec
[2020-11-28 12:28:50,659 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:28:50,667 INFO] number of examples: 3035
[2020-11-28 12:28:51,076 INFO] Step 2750/750000; acc:  91.30; ppl:  1.39; xent: 0.33; lr:

[2020-11-28 12:29:33,078 INFO] Step 4000/750000; acc:  93.13; ppl:  1.29; xent: 0.25; lr: 0.00100; 7595/27397 tok/s;    135 sec
[2020-11-28 12:29:34,182 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:29:34,190 INFO] number of examples: 3035
[2020-11-28 12:29:34,776 INFO] Step 4050/750000; acc:  93.16; ppl:  1.29; xent: 0.25; lr: 0.00100; 7644/27376 tok/s;    137 sec
[2020-11-28 12:29:35,795 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:29:35,802 INFO] number of examples: 3035
[2020-11-28 12:29:36,470 INFO] Step 4100/750000; acc:  93.31; ppl:  1.27; xent: 0.24; lr: 0.00100; 7816/27391 tok/s;    138 sec
[2020-11-28 12:29:37,404 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:29:37,412 INFO] number of examples: 3035
[2020-11-28 12:29:38,107 INFO] Step 4150/750000; acc:  92.86; ppl:  1.29; xent: 0.26; lr: 0.00100; 7811/27203 tok/s;    140 sec
[2020-11-28 12:29

[2020-11-28 12:30:20,178 INFO] Step 5400/750000; acc:  93.87; ppl:  1.25; xent: 0.22; lr: 0.00100; 7716/26608 tok/s;    182 sec
[2020-11-28 12:30:20,995 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:30:21,003 INFO] number of examples: 3035
[2020-11-28 12:30:21,814 INFO] Step 5450/750000; acc:  93.26; ppl:  1.27; xent: 0.24; lr: 0.00100; 7778/27320 tok/s;    184 sec
[2020-11-28 12:30:22,603 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:30:22,611 INFO] number of examples: 3035
[2020-11-28 12:30:23,475 INFO] Step 5500/750000; acc:  93.89; ppl:  1.24; xent: 0.22; lr: 0.00100; 7856/27315 tok/s;    185 sec
[2020-11-28 12:30:24,216 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 12:30:24,224 INFO] number of examples: 3035
[2020-11-28 12:30:25,143 INFO] Step 5550/750000; acc:  93.55; ppl:  1.26; xent: 0.23; lr: 0.00100; 7703/27378 tok/s;    187 sec
[2020-11-28 12:30

...

[2020-11-28 19:24:47,163 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:24:47,171 INFO] number of examples: 3035
[2020-11-28 19:24:47,560 INFO] Step 744300/750000; acc:  67.48; ppl:  9.65; xent: 2.27; lr: 0.00000; 7784/27314 tok/s;  25049 sec
[2020-11-28 19:24:48,781 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:24:48,789 INFO] number of examples: 3035
[2020-11-28 19:24:49,203 INFO] Step 744350/750000; acc:  67.32; ppl: 10.00; xent: 2.30; lr: 0.00000; 7859/27354 tok/s;  25051 sec
[2020-11-28 19:24:50,381 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:24:50,390 INFO] number of examples: 3035
[2020-11-28 19:24:50,880 INFO] Step 744400/750000; acc:  65.43; ppl: 11.00; xent: 2.40; lr: 0.00000; 7704/27790 tok/s;  25053 sec
[2020-11-28 19:24:51,980 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:24:51,988 INFO] number 

[2020-11-28 19:25:34,079 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:25:34,087 INFO] number of examples: 3035
[2020-11-28 19:25:34,756 INFO] Step 745700/750000; acc:  65.55; ppl: 11.35; xent: 2.43; lr: 0.00000; 7802/27343 tok/s;  25097 sec
[2020-11-28 19:25:35,691 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:25:35,713 INFO] number of examples: 3035
[2020-11-28 19:25:36,409 INFO] Step 745750/750000; acc:  66.73; ppl: 10.37; xent: 2.34; lr: 0.00000; 7733/26931 tok/s;  25098 sec
[2020-11-28 19:25:37,316 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:25:37,325 INFO] number of examples: 3035
[2020-11-28 19:25:38,114 INFO] Step 745800/750000; acc:  66.49; ppl: 10.84; xent: 2.38; lr: 0.00000; 7744/26702 tok/s;  25100 sec
[2020-11-28 19:25:38,932 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:25:38,940 INFO] number 

[2020-11-28 19:26:21,035 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:26:21,045 INFO] number of examples: 3035
[2020-11-28 19:26:21,922 INFO] Step 747100/750000; acc:  67.75; ppl:  9.67; xent: 2.27; lr: 0.00000; 7752/26955 tok/s;  25144 sec
[2020-11-28 19:26:22,661 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:26:22,684 INFO] number of examples: 3035
[2020-11-28 19:26:23,600 INFO] Step 747150/750000; acc:  67.04; ppl:  9.90; xent: 2.29; lr: 0.00000; 7658/27219 tok/s;  25145 sec
[2020-11-28 19:26:24,291 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:26:24,300 INFO] number of examples: 3035
[2020-11-28 19:26:25,294 INFO] Step 747200/750000; acc:  66.80; ppl: 10.05; xent: 2.31; lr: 0.00000; 7702/27140 tok/s;  25147 sec
[2020-11-28 19:26:25,911 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:26:25,919 INFO] number 

[2020-11-28 19:27:07,967 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:27:07,976 INFO] number of examples: 3035
[2020-11-28 19:27:09,103 INFO] Step 748500/750000; acc:  65.28; ppl: 11.87; xent: 2.47; lr: 0.00000; 7826/27129 tok/s;  25191 sec
[2020-11-28 19:27:09,580 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:27:09,589 INFO] number of examples: 3035
[2020-11-28 19:27:10,765 INFO] Step 748550/750000; acc:  67.28; ppl:  9.76; xent: 2.28; lr: 0.00000; 7657/27372 tok/s;  25193 sec
[2020-11-28 19:27:11,193 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:27:11,214 INFO] number of examples: 3035
[2020-11-28 19:27:12,443 INFO] Step 748600/750000; acc:  67.56; ppl:  9.67; xent: 2.27; lr: 0.00000; 7772/27108 tok/s;  25194 sec
[2020-11-28 19:27:12,820 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:27:12,829 INFO] number 

[2020-11-28 19:27:54,666 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:27:54,674 INFO] number of examples: 3035
[2020-11-28 19:27:56,040 INFO] Step 749900/750000; acc:  67.22; ppl: 10.03; xent: 2.31; lr: 0.00000; 7895/27349 tok/s;  25238 sec
[2020-11-28 19:27:56,269 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:27:56,278 INFO] number of examples: 3035
[2020-11-28 19:27:57,748 INFO] Step 749950/750000; acc:  66.22; ppl: 11.09; xent: 2.41; lr: 0.00000; 7543/26921 tok/s;  25240 sec
[2020-11-28 19:27:57,876 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.train.0.pt
[2020-11-28 19:27:57,900 INFO] number of examples: 3035
[2020-11-28 19:27:59,495 INFO] Step 750000/750000; acc:  65.22; ppl: 11.57; xent: 2.45; lr: 0.00000; 7521/26085 tok/s;  25241 sec
[2020-11-28 19:27:59,495 INFO] Loading dataset from /home/baoxiong/SY_269/models/model15k.valid.0.pt
[2020-11-28 19:27:59,497 INFO] number 

I had to reduce the validation batch size to 16 because of memory issues. The training took 17 hours. However, the process could have been stopped at an earlier time. Perplexity and accuracy plateaued early on, and subjectivally decent fake review generation results could be achieved with training times of only 2 hours.

Below you find some excerpts of the training log:

    [2019-06-12 09:05:51,800 INFO] Step 468700/750000; acc:  35.11; ppl: 24.87; xent: 3.21; lr: 0.00000; 11100/27825 tok/s;  38659 sec
    [2019-06-12 09:05:55,828 INFO] Step 468750/750000; acc:  34.51; ppl: 26.15; xent: 3.26; lr: 0.00000; 11981/27910 tok/s;  38663 sec
    [2019-06-12 09:05:55,829 INFO] Loading dataset from models/model15k.valid.0.pt
    [2019-06-12 09:05:56,043 INFO] number of examples: 15000
    [2019-06-12 09:09:38,355 INFO] Validation perplexity: 93.3477
    [2019-06-12 09:09:38,355 INFO] Validation accuracy: 24.1794
    
    ...

    [2019-06-12 15:34:42,982 INFO] Step 749850/750000; acc:  34.66; ppl: 25.92; xent: 3.26; lr: 0.00000; 11283/28185 tok/s;  61990 sec
    [2019-06-12 15:34:46,808 INFO] Step 749900/750000; acc:  34.88; ppl: 25.52; xent: 3.24; lr: 0.00000; 11560/28148 tok/s;  61994 sec
    [2019-06-12 15:34:50,988 INFO] Step 749950/750000; acc:  34.53; ppl: 25.97; xent: 3.26; lr: 0.00000; 10780/28526 tok/s;  61998 sec
    [2019-06-12 15:34:55,011 INFO] Step 750000/750000; acc:  34.82; ppl: 25.71; xent: 3.25; lr: 0.00000; 10835/28475 tok/s;  62002 sec
    [2019-06-12 15:34:55,012 INFO] Loading dataset from models/model15k.valid.0.pt
    [2019-06-12 15:34:55,229 INFO] number of examples: 15000
    [2019-06-12 15:38:36,945 INFO] Validation perplexity: 93.3476
    [2019-06-12 15:38:36,946 INFO] Validation accuracy: 24.1794
    [2019-06-12 15:38:37,472 INFO] Saving checkpoint models/model15k750k_step_750000.pt

## Fake review generation

To generate fake reviews, we can use the trained model and our adapted OpenNMT-py library. As a demonstration, below is the output of 40 random sentences picked from the test set. The model seems to be able to infer context specific knowledge such as places or categories and the appropriate sentiment - there are only a few incoherent  sentences or phrases.

An anectodal review with my friends seems to confirm that the reviews are of quite high quality and difficult to detect as fake.

Integrating more contextual information (business name or similar) into the training examples would probably improve the variety of the output.

In [9]:
!python /home/baoxiong/SY_269/OpenNMT-py/translate.py -model ../models/model15k750k_step_750000.pt -src test_context_excerpt.txt -replace_unk -verbose -max_length 50 -ignore_when_blocking "." "" "" "," "i" "thus" "our" "them" "they" "their" "them" "us" "we" "ours" "theirs" "she" "her" "hers" "him" "his" "my" "mine" "but" "and" "or" "/" ":" "it" "its" "if"  --beam_size 5


[2020-11-28 22:06:53,455 INFO] Translating shard 0.

SENT 1: ['4.0', 'las', 'vegas', 'restaurants', ',', 'vietnamese']
PRED 1: I would highly 4.0 for 4.0 but the beef restaurants had cheap restaurants
PRED SCORE: -5.2809

SENT 2: ['1.0', 'calgary', 'asian', 'fusion', ',', 'chicken', 'wings', ',', 'food', ',', 'cafes', ',', 'chinese', ',', 'desserts', ',', 'juice', 'bars', '&', 'smoothies', ',', 'restaurants']
PRED 2: we had the , , it was great and bars
PRED SCORE: -4.3279

SENT 3: ['3.0', 'scottsdale', 'japanese', ',', 'nightlife', ',', 'restaurants', ',', 'sushi', 'bars']
PRED 3: For the japanese sushi it is a little bars for your bars
PRED SCORE: -2.7106

SENT 4: ['1.0', 'phoenix', 'sandwiches', ',', 'beer', ',', 'wine', '&', 'spirits', ',', 'beer', 'bar', ',', 'bars', ',', 'breakfast', '&', 'brunch', ',', 'nightlife', ',', 'american', '-lrb-', 'new', '-rrb-', ',', 'burgers', ',', 'food', ',', 'restaurants']
PRED 4: 1.0 have a 1.0 beer dish and , beer prices.
PRED SCORE: -3.7259

SE

We can now use our test set to generate 6000 fake reviews.

In [10]:
!python ../OpenNMT-py/translate.py -model ../models/model15k750k_step_750000.pt -src ../data/test_context.txt -replace_unk -verbose -max_length 50 -ignore_when_blocking "." "" "" "," "i" "thus" "our" "them" "they" "their" "them" "us" "we" "ours" "theirs" "she" "her" "hers" "him" "his" "my" "mine" "but" "and" "or" "/" ":" "it" "its" "if"  --beam_size 5 --output fake-reviews/generated.txt

[2020-11-28 22:06:58,408 INFO] Translating shard 0.

SENT 1: ['food', 'positive', 'bread']
PRED 1: food is home to bread and bread rolls not to found bread bread
PRED SCORE: -0.9886

SENT 2: ['service', 'positive', 'delivery', 'times']
PRED 2: The service is a small service at least service
PRED SCORE: -2.5640

SENT 3: ['food', 'positive', 'Food']
PRED 3: Food was average but tasty.
PRED SCORE: -0.4698

SENT 4: ['food', 'positive', 'coffee']
PRED 4: Their coffee is quite good positive
PRED SCORE: -0.0002

SENT 5: ['food', 'conflict', 'ambience', 'positive', 'sushi', 'place']
PRED 5: Not a conflict for conflict as well as positive out.
PRED SCORE: -3.2333

SENT 6: ['anecdotes/miscellaneous', 'positive', 'people']
PRED 6: I love to visit anecdotes/miscellaneous for my boyfriend anecdotes/miscellaneous
PRED SCORE: -1.5970

SENT 7: ['food', 'positive', 'Japanese', 'food']
PRED 7: food food the best food food in positive food
PRED SCORE: -2.8117

SENT 8: ['food', 'positive', 'asian', 'salad


SENT 61: ['anecdotes/miscellaneous', 'positive']
PRED 61: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -3.3458

SENT 62: ['anecdotes/miscellaneous', 'positive']
PRED 62: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -3.3458

SENT 63: ['food', 'positive', 'price', 'positive', 'menu', 'priced']
PRED 63: positive of the menu are food and the price is even positive
PRED SCORE: -1.9072

SENT 64: ['food', 'positive', 'food', 'ingredients']
PRED 64: food food food is so positive food
PRED SCORE: -0.8414

SENT 65: ['food', 'negative', 'food']
PRED 65: The food was absolutely negative
PRED SCORE: -2.2087

SENT 66: ['food', 'positive', 'price', 'positive', 'Appetizer', 'meal']
PRED 66: food is around the Appetizer Appetizer it's food and the prices are so positive
PRED SCORE: -3.7411

SENT 67: ['food', 'positive', 'spicy', 'mussels']
PRED 67: My husband and I had enjoyed the mussels mussels
PRED SCORE: -2.2396

SENT 68: ['food', 'positive', 'Onion', 'Rings']
PRED 68


SENT 121: ['anecdotes/miscellaneous', 'negative']
PRED 121: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -4.0878

SENT 122: ['food', 'positive', 'price', 'positive', 'wraps', 'burgers', 'salads', 'mango', 'margareta']
PRED 122: The pizza is great and the prices are always positive
PRED SCORE: -3.5812

SENT 123: ['food', 'positive']
PRED 123: Everything at food Thai is tasty and positive
PRED SCORE: -3.0626

SENT 124: ['price', 'positive', 'prices']
PRED 124: and you can't price the prices.
PRED SCORE: -1.0967

SENT 125: ['service', 'positive', 'service']
PRED 125: The service was service
PRED SCORE: -2.6200

SENT 126: ['service', 'conflict', 'waiter', 'staff']
PRED 126: Service was conflict but the waiter waiter of waiter
PRED SCORE: -3.8953

SENT 127: ['ambience', 'negative', 'folding', 'chair']
PRED 127: The ambience is negative
PRED SCORE: -3.1875

SENT 128: ['anecdotes/miscellaneous', 'negative']
PRED 128: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: 


SENT 181: ['food', 'negative', 'hotdogs']
PRED 181: The hotdogs was just negative negative
PRED SCORE: -2.9160

SENT 182: ['service', 'positive', 'food', 'positive', 'staff', 'Saag', 'gosht']
PRED 182: service with the positive and positive are friendly and the food is positive positive
PRED SCORE: -3.9340

SENT 183: ['food', 'positive', 'garlic', 'knots']
PRED 183: Great garlic garlic food
PRED SCORE: -1.4347

SENT 184: ['food', 'positive', 'Indian', 'food']
PRED 184: I cannot food better Indian food in all of the city.
PRED SCORE: -0.2911

SENT 185: ['anecdotes/miscellaneous', 'positive']
PRED 185: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -3.3458

SENT 186: ['food', 'positive', 'pizza']
PRED 186: The pizza was pretty good and positive
PRED SCORE: -1.9710

SENT 187: ['anecdotes/miscellaneous', 'positive']
PRED 187: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -3.3458

SENT 188: ['ambience', 'negative', 'music']
PRED 188: ambience do people ambience a


SENT 241: ['price', 'neutral', 'service', 'neutral', 'lunch', 'take-out', 'dine-in']
PRED 241: We were neutral to the take-out lunch
PRED SCORE: -3.4325

SENT 242: ['anecdotes/miscellaneous', 'positive']
PRED 242: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -3.3458

SENT 243: ['anecdotes/miscellaneous', 'neutral']
PRED 243: anecdotes/miscellaneous anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -4.6450

SENT 244: ['price', 'positive']
PRED 244: And price
PRED SCORE: -1.8476

SENT 245: ['food', 'positive', 'food', 'fresh', 'juice', 'concoctions']
PRED 245: The food and fresh are the best fresh you can ever positive
PRED SCORE: -2.6291

SENT 246: ['food', 'positive', 'price', 'positive', 'food', 'prices']
PRED 246: In food the food is very good and the prices are food
PRED SCORE: -0.4469

SENT 247: ['ambience', 'positive', 'food', 'positive', 'place', 'soul', 'food']
PRED 247: If you go food the wait and the place it's ambience
PRED SCORE: -6.0662

SENT 248: 

...


SENT 541: ['food', 'neutral', 'boutique', 'selection', 'of', 'wines']
PRED 541: We ate there with the boutique of wines but of neutral
PRED SCORE: -3.8545

SENT 542: ['ambience', 'conflict']
PRED 542: ambience busy but fast conflict
PRED SCORE: -2.0902

SENT 543: ['food', 'positive', 'assortment', 'of', 'wraps', 'traditional', 'Mediterranean', 'fare']
PRED 543: The place is food of with a little of of the best of of positive all positive
PRED SCORE: -3.2369

SENT 544: ['food', 'positive', 'Fresh', 'veggies', 'middle', 'eastern', 'spreads', 'cheese', 'falafel', 'soup', 'fish', 'rice', 'root', 'vegetables', 'rice', 'medley', 'spinach', 'thing', 'lamb', 'kebabs', 'cheese', 'baclava', 'fooood']
PRED 544: I have food spinach spinach it had 2 rice and spreads
PRED SCORE: -5.2027

SENT 545: ['food', 'conflict', 'Saketini', 'bar', 'menu']
PRED 545: The menu is conflict but everything really conflict out of bar food
PRED SCORE: -3.2692

SENT 546: ['ambience', 'negative', 'look']
PRED 546: The 


SENT 601: ['price', 'positive', 'prices']
PRED 601: and you can't price the prices.
PRED SCORE: -1.0967

SENT 602: ['price', 'negative', 'bill', 'gratuity']
PRED 602: The price bill was a bit price but the experience was great.
PRED SCORE: -1.8376

SENT 603: ['food', 'conflict', 'halibut', 'cheek', 'appetizer', 'portion', 'of', 'foie', 'gras', 'meal']
PRED 603: They even have a portion with the appetizer appetizer and the portion were nice and foie
PRED SCORE: -4.7615

SENT 604: ['food', 'positive', 'Food', 'empenadas', 'plaintains', 'afternoon', 'snack']
PRED 604: Their empenadas are very empenadas and the empenadas snack empenadas
PRED SCORE: -2.6904

SENT 605: ['food', 'positive', 'pasta', 'specials', 'appetizer']
PRED 605: We had the specials which were great.
PRED SCORE: -2.1776

SENT 606: ['food', 'positive', 'Big', 'Mac', 'Chicken', 'McNuggets', 'Filet-O-Fish', 'sandwich', "McDonald's", 'famous', 'french', 'fries', 'entree-sized', 'salads']
PRED 606: We had a Mac fries fries I 


SENT 661: ['anecdotes/miscellaneous', 'negative']
PRED 661: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -4.0878

SENT 662: ['anecdotes/miscellaneous', 'negative']
PRED 662: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -4.0878

SENT 663: ['anecdotes/miscellaneous', 'neutral']
PRED 663: anecdotes/miscellaneous anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -4.6450

SENT 664: ['ambience', 'positive']
PRED 664: It's like you are ambience to the Italian ambience very romantic and positive with positive
PRED SCORE: -2.7870

SENT 665: ['service', 'positive', 'service']
PRED 665: The service was service
PRED SCORE: -2.6200

SENT 666: ['food', 'positive', 'food', 'wine', 'desserts']
PRED 666: The food is wine and the desserts is positive
PRED SCORE: -1.4879

SENT 667: ['anecdotes/miscellaneous', 'positive', 'dining', 'experience']
PRED 667: The entire dining experience was anecdotes/miscellaneous
PRED SCORE: -0.0005

SENT 668: ['anecdotes/miscellaneo


SENT 721: ['ambience', 'positive', 'atmosphere']
PRED 721: The atmosphere is much better than positive positive positive and positive
PRED SCORE: -1.2876

SENT 722: ['ambience', 'neutral', 'counter']
PRED 722: ambience this neutral two counter are counter counter neutral
PRED SCORE: -1.1478

SENT 723: ['anecdotes/miscellaneous', 'neutral', 'bottle', 'of', 'wine']
PRED 723: The wine that was neutral bottle and the cheese neutral of
PRED SCORE: -2.3092

SENT 724: ['anecdotes/miscellaneous', 'positive']
PRED 724: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -3.3458

SENT 725: ['anecdotes/miscellaneous', 'positive']
PRED 725: anecdotes/miscellaneous anecdotes/miscellaneous
PRED SCORE: -3.3458

SENT 726: ['food', 'positive', 'menu', 'Japanese', 'dishes', 'Foie', 'Gras', 'Unagi', 'Napolean', 'Jap', 'style', 'hamburger', 'steak', 'spicy', 'cod', 'roe', 'spaghetti', 'black', 'cod', 'with', 'miso', 'base', 'rack', 'of', 'lamb', 'in', 'black', 'truffle', 'sauce']
PRED 726: We pos


SENT 781: ['food', 'positive', 'anecdotes/miscellaneous', 'neutral', 'lunch', 'food']
PRED 781: I have eaten in food three times and the food is always neutral food good.
PRED SCORE: -2.9026

SENT 782: ['food', 'positive', 'seafood', 'Greek', 'food']
PRED 782: If you love seafood you would love this food
PRED SCORE: -1.9388

SENT 783: ['food', 'neutral', 'menu', 'burgers', 'steaks', 'shepherds', 'pie', 'portabella', 'lasagna', 'pub', 'fare']
PRED 783: neutral the menu with a burgers shepherds shepherds neutral but shepherds neutral neutral
PRED SCORE: -2.0991

SENT 784: ['food', 'neutral', 'price', 'negative', 'food', 'prices']
PRED 784: The food is negative and the prices here are price
PRED SCORE: -0.6951

SENT 785: ['food', 'neutral', 'service', 'negative', 'service', 'food']
PRED 785: The food service was just negative - nothing service - but the service was negative
PRED SCORE: -0.6675

SENT 786: ['food', 'neutral', 'price', 'negative', 'food', 'prices']
PRED 786: The food is neg